Alterações em relação ao modelo anterior:

- uso apenas de GridSearchCV
- criação da variável Family Size

A criação de Family Size melhorou o score, que foi de 0.77990 para 0.78947, posição 3742 (ganho de 1717 posições!).

<b>Próximos passos</b>

* Melhoria dos atributos. Com uso de CV, provavelmente as variáveis derivadas (de SibSp e Parch), que antes não trouxeram melhorias, agora podem trazer resultados, pois, conforme visto anteriormente, elas tem alguma correlação com a variável dependente.

* Mais um: no modelo inicial que fiz, retirava as variáveis com alto índice de NaN (Cabin, por exemplo); voltar a fazer isso, pois a contribuição dela é nula.

* Nos modelos de soluções disponibilizados na Internet, a variável Name permite a criação de derivações conforme o título da pessoa: Mr, Mrs, Miss etc. Verificar se isso pode trazer ganhos.


PS.: Resultado rodando com RandomizedSearchCV

- Variable: Sex                  Importance: 0.39
- Variable: Fare                 Importance: 0.11
- Variable: Ticket               Importance: 0.1
- Variable: Pclass               Importance: 0.09
- Variable: Age                  Importance: 0.09
- Variable: Cabin                Importance: 0.07
- Variable: PassengerId          Importance: 0.06
- Variable: SibSp                Importance: 0.02
- Variable: Parch                Importance: 0.02
- Variable: Embarked             Importance: 0.02
- Variable: Age_na               Importance: 0.01

Conforme suspeita inicial, Embarked não tem importância significativa no resultado. E foi confirmada também a pouca importância de SibSp e Parch. Cabin, que parecia não ter tanta importância, quase que equivale a Age.

In [1]:
%load_ext autoreload
%autoreload 2

%matplotlib inline

In [2]:
from fastai.imports import *
from fastai.structured import *

from pandas_summary import DataFrameSummary
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from IPython.display import display

from sklearn import metrics

In [3]:
PATH = "data/"

In [4]:
!ls {PATH}

gender_submission.csv  preds_without_PassengerId.csv  train.csv
preds.csv	       test.csv


Vamos ler o arquivo de treino!

In [4]:
df_raw = pd.read_csv(f'{PATH}train.csv')
df_test = pd.read_csv(f'{PATH}test.csv')

In [5]:
# juntar os 2 dataframes em um só facilita o pré-processamento
df_raw = df_raw.append(df_test, sort = False)

In [6]:
len(df_raw)

1309

In [7]:
def display_all(df):
    with pd.option_context("display.max_rows", 1000, "display.max_columns", 1000): 
        display(df)

In [8]:
df_raw.describe()

PassengerId    Survived       Pclass          Age        SibSp  \
count  1309.000000  891.000000  1309.000000  1046.000000  1309.000000   
mean    655.000000    0.383838     2.294882    29.881138     0.498854   
std     378.020061    0.486592     0.837836    14.413493     1.041658   
min       1.000000    0.000000     1.000000     0.170000     0.000000   
25%     328.000000    0.000000     2.000000    21.000000     0.000000   
50%     655.000000    0.000000     3.000000    28.000000     0.000000   
75%     982.000000    1.000000     3.000000    39.000000     1.000000   
max    1309.000000    1.000000     3.000000    80.000000     8.000000   

             Parch         Fare  
count  1309.000000  1308.000000  
mean      0.385027    33.295479  
std       0.865560    51.758668  
min       0.000000     0.000000  
25%       0.000000     7.895800  
50%       0.000000    14.454200  
75%       0.000000    31.275000  
max       9.000000   512.329200

In [13]:
display_all(df_raw)

PassengerId  Survived  Pclass  \
0              1       0.0       3   
1              2       1.0       1   
2              3       1.0       3   
3              4       1.0       1   
4              5       0.0       3   
5              6       0.0       3   
6              7       0.0       1   
7              8       0.0       3   
8              9       1.0       3   
9             10       1.0       2   
10            11       1.0       3   
11            12       1.0       1   
12            13       0.0       3   
13            14       0.0       3   
14            15       0.0       3   
15            16       1.0       2   
16            17       0.0       3   
17            18       1.0       2   
18            19       0.0       3   
19            20       1.0       3   
20            21       0.0       2   
21            22       1.0       2   
22            23       1.0       3   
23            24       1.0       1   
24            25       0.0       3   
25            26       1.0       3   
26            27       0.0       3   
27            28       0.0       1   
28            29       1.0       3   
29            30       0.0       3   
30            31       0.0       1   
31            32       1.0       1   
32            33       1.0       3   
33            34       0.0       2   
34            35       0.0       1   
35            36       0.0       1   
36            37       1.0       3   
37            38       0.0       3   
38            39       0.0       3   
39            40       1.0       3   
40            41       0.0       3   
41            42       0.0       2   
42            43       0.0       3   
43            44       1.0       2   
44            45       1.0       3   
45            46       0.0       3   
46            47       0.0       3   
47            48       1.0       3   
48            49       0.0       3   
49            50       0.0       3   
50            51       0.0       3   
51            52       0.0       3   
52            53       1.0       1   
53            54       1.0       2   
54            55       0.0       1   
55            56       1.0       1   
56            57       1.0       2   
57            58       0.0       3   
58            59       1.0       2   
59            60       0.0       3   
60            61       0.0       3   
61            62       1.0       1   
62            63       0.0       1   
63            64       0.0       3   
64            65       0.0       1   
65            66       1.0       3   
66            67       1.0       2   
67            68       0.0       3   
68            69       1.0       3   
69            70       0.0       3   
70            71       0.0       2   
71            72       0.0       3   
72            73       0.0       2   
73            74       0.0       3   
74            75       1.0       3   
75            76       0.0       3   
76            77       0.0       3   
77            78       0.0       3   
78            79       1.0       2   
79            80       1.0       3   
80            81       0.0       3   
81            82       1.0       3   
82            83       1.0       3   
83            84       0.0       1   
84            85       1.0       2   
85            86       1.0       3   
86            87       0.0       3   
87            88       0.0       3   
88            89       1.0       1   
89            90       0.0       3   
90            91       0.0       3   
91            92       0.0       3   
92            93       0.0       1   
93            94       0.0       3   
94            95       0.0       3   
95            96       0.0       3   
96            97       0.0       1   
97            98       1.0       1   
98            99       1.0       2   
99           100       0.0       2   
100          101       0.0       3   
101          102       0.0       3   
102          103       0.0       1   
103          104       0.0       3   
104          10

Temos que ajustar os dados.

- As colunas 'Name', <s>'Cabin', 'Ticket' e 'Embarked' (porto de embarcação)</s> e PassengerId, em princípio, não fazem sentido. Provavelmente nossa variável dependente não se relacionam com elas.
- A coluna 'Sex', 'Embarked' devem ser categorizadas.
- Também temos alguns NaN, que devem ser tratados (vide abaixo).

In [9]:
def drop_columns(df, cols):
    df_new = df.drop(columns =  cols)
    return df_new

In [10]:
(df_raw.isnull().sum()/len(df_raw)).sort_values(ascending=False)

Cabin          0.774637
Survived       0.319328
Age            0.200917
Embarked       0.001528
Fare           0.000764
Ticket         0.000000
Parch          0.000000
SibSp          0.000000
Sex            0.000000
Name           0.000000
Pclass         0.000000
PassengerId    0.000000
dtype: float64

As colunas Age, Cabin e Embarked contém valores inexistentes (<i>missing values</i>).

<i>Nota: a coluna Cabin possui uma alta porcentagem de missing values; além disso, ela não me parece trazer grande informação. Vamos adicioná-la a lista de colunas a serem dropadas.</i>

In [11]:
df_train = drop_columns(df_raw, ['Name', 'PassengerId', 'Cabin'])

In [9]:
df_train.tail()

Survived  Pclass     Sex   Age  SibSp  Parch              Ticket  \
413       NaN       3    male   NaN      0      0           A.5. 3236   
414       NaN       1  female  39.0      0      0            PC 17758   
415       NaN       3    male  38.5      0      0  SOTON/O.Q. 3101262   
416       NaN       3    male   NaN      0      0              359309   
417       NaN       3    male   NaN      1      1                2668   

         Fare Embarked  
413    8.0500        S  
414  108.9000        C  
415    7.2500        S  
416    8.0500        S  
417   22.3583        C

In [12]:
# convertendo para categorias Pandas
train_cats(df_train)

In [13]:
df_train.Sex = df_train.Sex.cat.codes
df_train.Ticket = df_train.Ticket.cat.codes
df_train.Embarked = df_train.Embarked.cat.codes

In [14]:
display_all(df_train)

Survived  Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked
0         0.0       3    1  22.00      1      0     720    7.2500         2
1         1.0       1    0  38.00      1      0     816   71.2833         0
2         1.0       3    0  26.00      0      0     914    7.9250         2
3         1.0       1    0  35.00      1      0      65   53.1000         2
4         0.0       3    1  35.00      0      0     649    8.0500         2
5         0.0       3    1    NaN      0      0     373    8.4583         1
6         0.0       1    1  54.00      0      0     109   51.8625         2
7         0.0       3    1   2.00      3      1     541   21.0750         2
8         1.0       3    0  27.00      0      2     477   11.1333         2
9         1.0       2    0  14.00      1      0     174   30.0708         0
10        1.0       3    0   4.00      1      1     839   16.7000         2
11        1.0       1    0  58.00      0      0      50   26.5500         2
12        0.0       3    1  20.00      0      0     733    8.0500         2
13        0.0       3    1  39.00      1      5     459   31.2750         2
14        0.0       3    0  14.00      0      0     566    7.8542         2
15        1.0       2    0  55.00      0      0     204   16.0000         2
16        0.0       3    1   2.00      4      1     659   29.1250         1
17        1.0       2    1    NaN      0      0     201   13.0000         2
18        0.0       3    0  31.00      1      0     417   18.0000         2
19        1.0       3    0    NaN      0      0     243    7.2250         0
20        0.0       2    1  35.00      0      0     182   26.0000         2
21        1.0       2    1  34.00      0      0     203   13.0000         2
22        1.0       3    0  15.00      0      0     379    8.0292         1
23        1.0       1    1  28.00      0      0      54   35.5000         2
24        0.0       3    0   8.00      3      1     541   21.0750         2
25        1.0       3    0  38.00      1      5     454   31.3875         2
26        0.0       3    1    NaN      0      0     238    7.2250         0
27        0.0       1    1  19.00      3      2     123  263.0000         2
28        1.0       3    0    NaN      0      0     385    7.8792         1
29        0.0       3    1    NaN      0      0     499    7.8958         2
30        0.0       1    1  40.00      0      0     818   27.7208         0
31        1.0       1    0    NaN      1      0     802  146.5208         0
32        1.0       3    0    NaN      0      0     397    7.7500         1
33        0.0       2    1  66.00      0      0     751   10.5000         2
34        0.0       1    1  28.00      1      0     820   82.1708         0
35        0.0       1    1  42.00      1      0      55   52.0000         2
36        1.0       3    1    NaN      0      0     272    7.2292         0
37        0.0       3    1  21.00      0      0     706    8.0500         2
38        0.0       3    0  18.00      2      0     418   18.0000         2
39        1.0       3    0  14.00      1      0     245   11.2417         0
40        0.0       3    0  40.00      1      0     695    9.4750         2
41        0.0       2    0  27.00      1      0      69   21.0000         2
42        0.0       3    1    NaN      0      0     536    7.8958         0
43        1.0       2    0   3.00      1      2     868   41.5792         0
44        1.0       3    0  19.00      0      0     384    7.8792         1
45        0.0       3    1    NaN      0      0     840    8.0500         2
46        0.0       3    1    NaN      1      0     637   15.5000         1
47        1.0       3    0    NaN      0      0     100    7.7500         1
48        0.0       3    1    NaN      2      0     256   21.6792         0
49        0.0       3    0  18.00      1      0     520   17.8000         2
50        0.0       3    1   7.00      4      1     335   39.6875         2
51        0.0       3    1  21.00      0      0     7

As colunas SibSp e Parch podem ter correlação com a  chance de sobrevivência. Com isso, vamos agrupá-las e criar a variável 'Family Size'.

In [15]:
df_train['Family Size'] = df_train.SibSp + df_train.Parch

In [16]:
display_all(df_train)

Survived  Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  \
0         0.0       3    1  22.00      1      0     720    7.2500         2   
1         1.0       1    0  38.00      1      0     816   71.2833         0   
2         1.0       3    0  26.00      0      0     914    7.9250         2   
3         1.0       1    0  35.00      1      0      65   53.1000         2   
4         0.0       3    1  35.00      0      0     649    8.0500         2   
5         0.0       3    1    NaN      0      0     373    8.4583         1   
6         0.0       1    1  54.00      0      0     109   51.8625         2   
7         0.0       3    1   2.00      3      1     541   21.0750         2   
8         1.0       3    0  27.00      0      2     477   11.1333         2   
9         1.0       2    0  14.00      1      0     174   30.0708         0   
10        1.0       3    0   4.00      1      1     839   16.7000         2   
11        1.0       1    0  58.00      0      0      50   26.5500         2   
12        0.0       3    1  20.00      0      0     733    8.0500         2   
13        0.0       3    1  39.00      1      5     459   31.2750         2   
14        0.0       3    0  14.00      0      0     566    7.8542         2   
15        1.0       2    0  55.00      0      0     204   16.0000         2   
16        0.0       3    1   2.00      4      1     659   29.1250         1   
17        1.0       2    1    NaN      0      0     201   13.0000         2   
18        0.0       3    0  31.00      1      0     417   18.0000         2   
19        1.0       3    0    NaN      0      0     243    7.2250         0   
20        0.0       2    1  35.00      0      0     182   26.0000         2   
21        1.0       2    1  34.00      0      0     203   13.0000         2   
22        1.0       3    0  15.00      0      0     379    8.0292         1   
23        1.0       1    1  28.00      0      0      54   35.5000         2   
24        0.0       3    0   8.00      3      1     541   21.0750         2   
25        1.0       3    0  38.00      1      5     454   31.3875         2   
26        0.0       3    1    NaN      0      0     238    7.2250         0   
27        0.0       1    1  19.00      3      2     123  263.0000         2   
28        1.0       3    0    NaN      0      0     385    7.8792         1   
29        0.0       3    1    NaN      0      0     499    7.8958         2   
30        0.0       1    1  40.00      0      0     818   27.7208         0   
31        1.0       1    0    NaN      1      0     802  146.5208         0   
32        1.0       3    0    NaN      0      0     397    7.7500         1   
33        0.0       2    1  66.00      0      0     751   10.5000         2   
34        0.0       1    1  28.00      1      0     820   82.1708         0   
35        0.0       1    1  42.00      1      0      55   52.0000         2   
36        1.0       3    1    NaN      0      0     272    7.2292         0   
37        0.0       3    1  21.00      0      0     706    8.0500         2   
38        0.0       3    0  18.00      2      0     418   18.0000         2   
39        1.0       3    0  14.00      1      0     245   11.2417         0   
40        0.0       3    0  40.00      1      0     695    9.4750         2   
41        0.0       2    0  27.00      1      0      69   21.0000         2   
42        0.0       3    1    NaN      0      0     536    7.8958         0   
43        1.0       2    0   3.00      1      2     868   41.5792         0   
44        1.0       3    0  19.00      0      0     384    7.8792         1   
45        0.0       3    1    NaN      0      0     840    8.0500         2   
46        0.0       3    1    NaN      1      0     637   15.5000         1   
47        1.0       3    0    NaN      0      0     100    7.7500         1   
48        0.0       3    1    NaN      2      0     256   21.6792         0   
49        0.0       3    0  18.00      1      0     520

In [17]:
df_test = df_train.iloc[891:].copy()
df_train = df_train.iloc[:891].copy()

In [18]:
len(df_train)

891

In [19]:
df, y, nas = proc_df(df_train, 'Survived')

In [20]:
display_all(df)

Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  \
0         3    1  22.00      1      0     720    7.2500         2   
1         1    0  38.00      1      0     816   71.2833         0   
2         3    0  26.00      0      0     914    7.9250         2   
3         1    0  35.00      1      0      65   53.1000         2   
4         3    1  35.00      0      0     649    8.0500         2   
5         3    1  28.00      0      0     373    8.4583         1   
6         1    1  54.00      0      0     109   51.8625         2   
7         3    1   2.00      3      1     541   21.0750         2   
8         3    0  27.00      0      2     477   11.1333         2   
9         2    0  14.00      1      0     174   30.0708         0   
10        3    0   4.00      1      1     839   16.7000         2   
11        1    0  58.00      0      0      50   26.5500         2   
12        3    1  20.00      0      0     733    8.0500         2   
13        3    1  39.00      1      5     459   31.2750         2   
14        3    0  14.00      0      0     566    7.8542         2   
15        2    0  55.00      0      0     204   16.0000         2   
16        3    1   2.00      4      1     659   29.1250         1   
17        2    1  28.00      0      0     201   13.0000         2   
18        3    0  31.00      1      0     417   18.0000         2   
19        3    0  28.00      0      0     243    7.2250         0   
20        2    1  35.00      0      0     182   26.0000         2   
21        2    1  34.00      0      0     203   13.0000         2   
22        3    0  15.00      0      0     379    8.0292         1   
23        1    1  28.00      0      0      54   35.5000         2   
24        3    0   8.00      3      1     541   21.0750         2   
25        3    0  38.00      1      5     454   31.3875         2   
26        3    1  28.00      0      0     238    7.2250         0   
27        1    1  19.00      3      2     123  263.0000         2   
28        3    0  28.00      0      0     385    7.8792         1   
29        3    1  28.00      0      0     499    7.8958         2   
30        1    1  40.00      0      0     818   27.7208         0   
31        1    0  28.00      1      0     802  146.5208         0   
32        3    0  28.00      0      0     397    7.7500         1   
33        2    1  66.00      0      0     751   10.5000         2   
34        1    1  28.00      1      0     820   82.1708         0   
35        1    1  42.00      1      0      55   52.0000         2   
36        3    1  28.00      0      0     272    7.2292         0   
37        3    1  21.00      0      0     706    8.0500         2   
38        3    0  18.00      2      0     418   18.0000         2   
39        3    0  14.00      1      0     245   11.2417         0   
40        3    0  40.00      1      0     695    9.4750         2   
41        2    0  27.00      1      0      69   21.0000         2   
42        3    1  28.00      0      0     536    7.8958         0   
43        2    0   3.00      1      2     868   41.5792         0   
44        3    0  19.00      0      0     384    7.8792         1   
45        3    1  28.00      0      0     840    8.0500         2   
46        3    1  28.00      1      0     637   15.5000         1   
47        3    0  28.00      0      0     100    7.7500         1   
48        3    1  28.00      2      0     256   21.6792         0   
49        3    0  18.00      1      0     520   17.8000         2   
50        3    1   7.00      4      1     335   39.6875         2   
51        3    1  21.00      0      0     718    7.8000         2   
52        1    0  49.00      1      0     803   76.7292         0   
53        2    0  29.00      1      0     324   26.0000         2   
54        1    1  65.00      0      1      39   61.9792         0   
55        1    1  28.00      0      0     122   35.5000         2   
56        2    0  21.00      0      0     758   10.5000         2   
57 

In [21]:
# para efeitos de teste, dropar Age_na
df.drop(columns='Age_na', inplace=True)

In [22]:
display_all(df)

Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  Family Size
0         3    1  22.00      1      0     720    7.2500         2            1
1         1    0  38.00      1      0     816   71.2833         0            1
2         3    0  26.00      0      0     914    7.9250         2            0
3         1    0  35.00      1      0      65   53.1000         2            1
4         3    1  35.00      0      0     649    8.0500         2            0
5         3    1  28.00      0      0     373    8.4583         1            0
6         1    1  54.00      0      0     109   51.8625         2            0
7         3    1   2.00      3      1     541   21.0750         2            4
8         3    0  27.00      0      2     477   11.1333         2            2
9         2    0  14.00      1      0     174   30.0708         0            1
10        3    0   4.00      1      1     839   16.7000         2            2
11        1    0  58.00      0      0      50   26.5500         2            0
12        3    1  20.00      0      0     733    8.0500         2            0
13        3    1  39.00      1      5     459   31.2750         2            6
14        3    0  14.00      0      0     566    7.8542         2            0
15        2    0  55.00      0      0     204   16.0000         2            0
16        3    1   2.00      4      1     659   29.1250         1            5
17        2    1  28.00      0      0     201   13.0000         2            0
18        3    0  31.00      1      0     417   18.0000         2            1
19        3    0  28.00      0      0     243    7.2250         0            0
20        2    1  35.00      0      0     182   26.0000         2            0
21        2    1  34.00      0      0     203   13.0000         2            0
22        3    0  15.00      0      0     379    8.0292         1            0
23        1    1  28.00      0      0      54   35.5000         2            0
24        3    0   8.00      3      1     541   21.0750         2            4
25        3    0  38.00      1      5     454   31.3875         2            6
26        3    1  28.00      0      0     238    7.2250         0            0
27        1    1  19.00      3      2     123  263.0000         2            5
28        3    0  28.00      0      0     385    7.8792         1            0
29        3    1  28.00      0      0     499    7.8958         2            0
30        1    1  40.00      0      0     818   27.7208         0            0
31        1    0  28.00      1      0     802  146.5208         0            1
32        3    0  28.00      0      0     397    7.7500         1            0
33        2    1  66.00      0      0     751   10.5000         2            0
34        1    1  28.00      1      0     820   82.1708         0            1
35        1    1  42.00      1      0      55   52.0000         2            1
36        3    1  28.00      0      0     272    7.2292         0            0
37        3    1  21.00      0      0     706    8.0500         2            0
38        3    0  18.00      2      0     418   18.0000         2            2
39        3    0  14.00      1      0     245   11.2417         0            1
40        3    0  40.00      1      0     695    9.4750         2            1
41        2    0  27.00      1      0      69   21.0000         2            1
42        3    1  28.00      0      0     536    7.8958         0            0
43        2    0   3.00      1      2     868   41.5792         0            3
44        3    0  19.00      0      0     384    7.8792         1            0
45        3    1  28.00      0      0     840    8.0500         2            0
46        3    1  28.00      1      0     637   15.5000         1            1
47        3    0  28.00      0      0     100    7.7500         1            0
48        3    1  28.00      2      0     256   21.6792         0            2
49        3    0  18.00      1      0     520   17.8000

In [23]:
m = RandomForestClassifier(n_jobs=-1)
m.fit(df,y)
m.score(df,y)

0.9820426487093153

In [24]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(df, y, test_size = 0.20, random_state = 42)
X_train.shape, y_train.shape, X_test.shape

((712, 9), (712,), (179, 9))

In [25]:
def print_score(m, metrics = metrics):
    res = [metrics.accuracy_score(y_train, m.predict(X_train)), metrics.accuracy_score(y_test, m.predict(X_test))]
    if hasattr(m, 'oob_score_'): res.append(m.oob_score_)
    print(res)

In [26]:
m = RandomForestClassifier(n_jobs=-1)
m.fit(X_train,y_train)
print_score(m)

[0.9775280898876404, 0.7877094972067039]


Estamos com <b>overfitting</b>; a diferença entre o erro no treinamento e teste é considerável.

Vamos tentar aumentando o número de árvores.

In [27]:
m = RandomForestClassifier(n_jobs=-1, n_estimators=20)
m.fit(X_train,y_train)
print_score(m)

[0.9901685393258427, 0.8268156424581006]


In [28]:
m = RandomForestClassifier(n_jobs=-1, n_estimators=100, oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.9985955056179775, 0.8212290502793296, 0.8188202247191011]


In [29]:
m = RandomForestClassifier(n_jobs=-1, n_estimators=1000, oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.9985955056179775, 0.8156424581005587, 0.8286516853932584]


In [20]:
# voltando ao algoritmo inicial, com o número de árvores padrão
m = RandomForestClassifier(n_jobs=-1)
m.fit(X_train,y_train)
print_score(m)

[0.9805389221556886, 0.8161434977578476]


Vamos tentar usar <b>subsampling</b>.

Temos 891 linhas. Subsampling de 100.

In [143]:
len(df)

891

In [30]:
set_rf_samples(100)

Vamos combinar com o aumento do número de árvores para ver o que acontece.

In [31]:
m = RandomForestClassifier(n_jobs=-1, n_estimators=1000, oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.8735955056179775, 0.8044692737430168, 0.8258426966292135]


In [24]:
# modificar o subsampling
reset_rf_samples()
set_rf_samples(50)

In [25]:
m = RandomForestClassifier(n_jobs=-1, n_estimators=1000, oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.8502994011976048, 0.7982062780269058, 0.7994011976047904]


In [26]:
#modificar o subsampling
reset_rf_samples()
set_rf_samples(150)

In [27]:
m = RandomForestClassifier(n_jobs=-1,n_estimators=1000,  oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.9116766467065869, 0.8116591928251121, 0.8158682634730539]


Vamos tentar melhorar com <b>ajuste de parâmetros.</b>

In [32]:
reset_rf_samples()
m = RandomForestClassifier(n_jobs=-1,n_estimators=1000,  oob_score=True)
m.fit(X_train,y_train)
print_score(m)

[0.9985955056179775, 0.8156424581005587, 0.824438202247191]


Quero verificar se o conjunto que temos é não balanceado.

In [33]:
df_temp = pd.read_csv(f'{PATH}train.csv')
survived = len(df_temp.loc[df_temp['Survived']==1])
not_survived = len(df_temp.loc[df_temp['Survived']==0])
print(survived/len(df_temp), not_survived/len(df_temp))

0.3838383838383838 0.6161616161616161


O conjunto é de certa forma não balanceado (# classes positivas é consideravelemnte menor do que o de classes negativas).
http://www.chioka.in/class-imbalance-problem/

Nesse caso, conforme apresentado em https://www.analyticsvidhya.com/blog/2016/04/complete-tutorial-tree-based-modeling-scratch-in-python/, é aconselhável escolher um valor baixo para min_samples_leaf.

In [29]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=10)
m.fit(X_train, y_train)
print_score(m)

[0.874251497005988, 0.8071748878923767, 0.8023952095808383]


In [30]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5)
m.fit(X_train, y_train)
print_score(m)

[0.905688622754491, 0.8251121076233184, 0.8143712574850299]


In [31]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=2)
m.fit(X_train, y_train)
print_score(m)

[0.9520958083832335, 0.8251121076233184, 0.8218562874251497]


In [38]:
# utilizando o min_sample_leaf sozinho
m = RandomForestClassifier(n_jobs=-1, min_samples_leaf=5)
m.fit(X_train, y_train)
print_score(m)

/home/andre/anaconda3/envs/fastai-cpu/lib/python3.6/site-packages/sklearn/ensemble/forest.py:453: UserWarning: Some inputs do not have OOB scores. This probably means too few trees were used to compute any reliable oob estimates.
  warn("Some inputs do not have OOB scores. "
/home/andre/anaconda3/envs/fastai-cpu/lib/python3.6/site-packages/sklearn/ensemble/forest.py:458: RuntimeWarning: invalid value encountered in true_divide
  predictions[k].sum(axis=1)[:, np.newaxis])


[0.8847305389221557, 0.8430493273542601, 0.7904191616766467]


In [32]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5)
m.fit(X_train, y_train)
print_score(m)

[0.9011976047904192, 0.8251121076233184, 0.811377245508982]


Com min_samples_leaf=5 <s>min_samples_leaf=10</s>, reduzimos o overfitting e melhoramos um pouco um resultado final.

Vamos combinar com o parâmetro max_features.

Conforme discutido em https://www.analyticsvidhya.com/blog/2016/04/complete-tutorial-tree-based-modeling-scratch-in-python/, sqrt costuma funcionar muito bem. Mas vale a pena tentar também com 30 a 40% das features.

In [33]:
# combinando com max_features
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5, max_features=0.30)
m.fit(X_train, y_train)
print_score(m)

[0.8997005988023952, 0.820627802690583, 0.8038922155688623]


In [47]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5, max_features=0.35)
m.fit(X_train, y_train)
print_score(m)

[0.8932584269662921, 0.8491620111731844, 0.8132022471910112]


In [41]:
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5, max_features=0.40)
m.fit(X_train, y_train)
print_score(m)

[0.9041916167664671, 0.820627802690583, 0.811377245508982]


<s>Com os valores entre 30 e 40% das features, o score final não foi muito diferente daquele sem a presença do parâmetro.</s>

Os valores de 30 a 40% colocaram uma melhora no resultado.

In [42]:
# combinando com max_features 'sqrt' - esse o valor default do parâmetro
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5, max_features='sqrt')
m.fit(X_train, y_train)
print_score(m)

[0.905688622754491, 0.8161434977578476, 0.8158682634730539]


In [51]:
# combinando com max_features
m = RandomForestClassifier(n_estimators=1000, n_jobs=-1, oob_score=True, min_samples_leaf=5, max_features='log2')
m.fit(X_train, y_train)
print_score(m)

[0.8904494382022472, 0.8491620111731844, 0.8061797752808989]


A melhor combinação, aparentemente, foi com 1000 árvores, min_samples_leaf = <s>10</s> 5  e max_features = 'sqrt'.

Combinar com subsampling para ver se há alguma melhoria.

Subsampling de 600 <s>650</s> melhorou um pouco resultado (> overfitting, < accuracy e < oob-score)

Vamos adotar esse modelo e rodar para o set de test.

### Descoberta de features importantes

O trecho abaixo nos permite idendificar as <i>features</i> mais importantes.

In [52]:
feature_list = list(df.columns)
# Get numerical feature importances
importances = list(m.feature_importances_)
# List of tuples with variable and importance
feature_importances = [(feature, round(importance, 2)) for feature, importance in zip(feature_list, importances)]
# Sort the feature importances by most important first
feature_importances = sorted(feature_importances, key = lambda x: x[1], reverse = True)
# Print out the feature and importances 
[print('Variable: {:20} Importance: {}'.format(*pair)) for pair in feature_importances];

Variable: Sex                  Importance: 0.33
Variable: Ticket               Importance: 0.18
Variable: Fare                 Importance: 0.16
Variable: Age                  Importance: 0.14
Variable: Pclass               Importance: 0.08
Variable: Family Size          Importance: 0.05
Variable: SibSp                Importance: 0.02
Variable: Parch                Importance: 0.02
Variable: Embarked             Importance: 0.02


### Melhorando a descoberta de hiperparâmetros

O processo que fizemos até agora - tuning de min_samples_leaf, max_features, n_estimators - é muito manual, pouco produtivo e de certa forma ineficaz. A RandomForest nos fornece diversos parâmetros e descobrir manualmente qual é a melhor combinação entre eles é praticamente impossível - apesar de termos algumas intuições, que usamos até agora.

Sckit learn nos fornece uma maneira melhor de descobrir uma combinação desses parâmetros: RandomizedSearchCV. Essa pesquisa faz uso de CV e escolhe randomicamente os valores dentre os que especificamos no random_grid abaixo.

Vamos utilizar essa ferramenta para tentar descobrir a melhor combinação de hiper parâmetros.

In [35]:
from sklearn.model_selection import RandomizedSearchCV
# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 200, stop = 2000, num = 10)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt', 0.3, 0.4]
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(10, 110, num = 11)]
max_depth.append(None)
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 4, 5, 10, 20]
# Method of selecting samples for training each tree
bootstrap = [True, False]
# Create the random grid
random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}
print(random_grid)

{'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000], 'max_features': ['auto', 'sqrt', 0.3, 0.4], 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None], 'min_samples_split': [2, 5, 10], 'min_samples_leaf': [1, 2, 4, 5, 10, 20], 'bootstrap': [True, False]}


In [40]:
# vou combinar com subsampling para tentar acelerar o processo
reset_rf_samples()
#set_rf_samples(150)

In [41]:
# Use the random grid to search for best hyperparameters
# First create the base model to tune
rf = RandomForestClassifier()
# Random search of parameters, using 3 fold cross validation, 
# search across 100 different combinations, and use all available cores
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid, n_iter = 100, cv = 3, verbose=2, random_state=42, n_jobs = -1)
# Fit the random search model
rf_random.fit(X_train, y_train)

Fitting 3 folds for each of 100 candidates, totalling 300 fits
[CV] n_estimators=1200, min_samples_split=5, min_samples_leaf=10, max_features=0.4, max_depth=100, bootstrap=False 
[CV] n_estimators=1200, min_samples_split=5, min_samples_leaf=10, max_features=0.4, max_depth=100, bootstrap=False 
[CV]  n_estimators=1200, min_samples_split=5, min_samples_leaf=10, max_features=0.4, max_depth=100, bootstrap=False, total=   2.7s
[CV] n_estimators=1200, min_samples_split=5, min_samples_leaf=10, max_features=0.4, max_depth=100, bootstrap=False 
[CV]  n_estimators=1200, min_samples_split=5, min_samples_leaf=10, max_features=0.4, max_depth=100, bootstrap=False, total=   2.9s
[CV] n_estimators=200, min_samples_split=10, min_samples_leaf=10, max_features=auto, max_depth=20, bootstrap=True 
[CV]  n_estimators=200, min_samples_split=10, min_samples_leaf=10, max_features=auto, max_depth=20, bootstrap=True, total=   0.8s
[CV] n_estimators=200, min_samples_split=10, min_samples_leaf=10, max_features=aut

[CV] n_estimators=600, min_samples_split=5, min_samples_leaf=2, max_features=0.3, max_depth=None, bootstrap=True 
[CV]  n_estimators=600, min_samples_split=5, min_samples_leaf=2, max_features=0.3, max_depth=None, bootstrap=True, total=   1.3s
[CV] n_estimators=600, min_samples_split=5, min_samples_leaf=2, max_features=0.3, max_depth=None, bootstrap=True 
[CV]  n_estimators=600, min_samples_split=5, min_samples_leaf=2, max_features=0.3, max_depth=None, bootstrap=True, total=   1.3s
[CV] n_estimators=1200, min_samples_split=2, min_samples_leaf=4, max_features=sqrt, max_depth=30, bootstrap=True 
[CV]  n_estimators=600, min_samples_split=5, min_samples_leaf=2, max_features=0.3, max_depth=None, bootstrap=True, total=   1.3s
[CV] n_estimators=1200, min_samples_split=2, min_samples_leaf=4, max_features=sqrt, max_depth=30, bootstrap=True 
[CV]  n_estimators=1200, min_samples_split=2, min_samples_leaf=4, max_features=sqrt, max_depth=30, bootstrap=True, total=   2.5s
[CV] n_estimators=1200, min_

[Parallel(n_jobs=-1)]: Done  37 tasks      | elapsed:   36.1s


[CV]  n_estimators=1200, min_samples_split=2, min_samples_leaf=4, max_features=sqrt, max_depth=30, bootstrap=True, total=   2.5s
[CV] n_estimators=2000, min_samples_split=5, min_samples_leaf=2, max_features=auto, max_depth=20, bootstrap=True 
[CV]  n_estimators=1200, min_samples_split=2, min_samples_leaf=4, max_features=sqrt, max_depth=30, bootstrap=True, total=   2.5s
[CV] n_estimators=2000, min_samples_split=5, min_samples_leaf=2, max_features=auto, max_depth=20, bootstrap=True 
[CV]  n_estimators=2000, min_samples_split=5, min_samples_leaf=2, max_features=auto, max_depth=20, bootstrap=True, total=   4.6s
[CV] n_estimators=2000, min_samples_split=5, min_samples_leaf=2, max_features=auto, max_depth=20, bootstrap=True 
[CV]  n_estimators=2000, min_samples_split=5, min_samples_leaf=2, max_features=auto, max_depth=20, bootstrap=True, total=   4.6s
[CV] n_estimators=800, min_samples_split=2, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True 
[CV]  n_estimators=800, min_s

[CV]  n_estimators=2000, min_samples_split=2, min_samples_leaf=5, max_features=0.3, max_depth=30, bootstrap=True, total=   4.0s
[CV] n_estimators=1600, min_samples_split=2, min_samples_leaf=1, max_features=0.4, max_depth=20, bootstrap=True 
[CV]  n_estimators=1600, min_samples_split=2, min_samples_leaf=1, max_features=0.4, max_depth=20, bootstrap=True, total=   3.5s
[CV] n_estimators=1600, min_samples_split=2, min_samples_leaf=1, max_features=0.4, max_depth=20, bootstrap=True 
[CV]  n_estimators=1600, min_samples_split=2, min_samples_leaf=1, max_features=0.4, max_depth=20, bootstrap=True, total=   3.5s
[CV] n_estimators=1000, min_samples_split=10, min_samples_leaf=2, max_features=0.4, max_depth=40, bootstrap=False 
[CV]  n_estimators=1600, min_samples_split=2, min_samples_leaf=1, max_features=0.4, max_depth=20, bootstrap=True, total=   3.5s
[CV] n_estimators=1000, min_samples_split=10, min_samples_leaf=2, max_features=0.4, max_depth=40, bootstrap=False 
[CV]  n_estimators=1000, min_sam

...

[CV]  n_estimators=600, min_samples_split=2, min_samples_leaf=10, max_features=sqrt, max_depth=100, bootstrap=False, total=   1.2s
[CV] n_estimators=1800, min_samples_split=2, min_samples_leaf=2, max_features=sqrt, max_depth=80, bootstrap=True 
[CV]  n_estimators=600, min_samples_split=2, min_samples_leaf=10, max_features=sqrt, max_depth=100, bootstrap=False, total=   1.3s
[CV] n_estimators=1800, min_samples_split=2, min_samples_leaf=2, max_features=sqrt, max_depth=80, bootstrap=True 
[CV]  n_estimators=1800, min_samples_split=2, min_samples_leaf=2, max_features=sqrt, max_depth=80, bootstrap=True, total=   4.4s
[CV] n_estimators=1800, min_samples_split=2, min_samples_leaf=2, max_features=sqrt, max_depth=80, bootstrap=True 
[CV]  n_estimators=1800, min_samples_split=2, min_samples_leaf=2, max_features=sqrt, max_depth=80, bootstrap=True, total=   4.4s
[CV] n_estimators=1400, min_samples_split=5, min_samples_leaf=4, max_features=sqrt, max_depth=100, bootstrap=True 
[CV]  n_estimators=1800

[CV]  n_estimators=1200, min_samples_split=10, min_samples_leaf=10, max_features=auto, max_depth=100, bootstrap=False, total=   2.5s
[CV] n_estimators=1000, min_samples_split=10, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True 
[CV]  n_estimators=1000, min_samples_split=10, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True, total=   2.0s
[CV] n_estimators=1000, min_samples_split=10, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True 
[CV]  n_estimators=1000, min_samples_split=10, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True, total=   2.1s
[CV] n_estimators=1600, min_samples_split=5, min_samples_leaf=10, max_features=sqrt, max_depth=50, bootstrap=False 
[CV]  n_estimators=1000, min_samples_split=10, min_samples_leaf=5, max_features=sqrt, max_depth=40, bootstrap=True, total=   2.0s
[CV] n_estimators=1600, min_samples_split=5, min_samples_leaf=10, max_features=sqrt, max_depth=50, bootstrap=False 
[CV]  n_estimat

[CV] n_estimators=1200, min_samples_split=10, min_samples_leaf=4, max_features=0.3, max_depth=60, bootstrap=False 
[CV]  n_estimators=1200, min_samples_split=10, min_samples_leaf=4, max_features=0.3, max_depth=60, bootstrap=False, total=   2.5s
[CV] n_estimators=1200, min_samples_split=10, min_samples_leaf=4, max_features=0.3, max_depth=60, bootstrap=False 
[CV]  n_estimators=1200, min_samples_split=10, min_samples_leaf=4, max_features=0.3, max_depth=60, bootstrap=False, total=   2.5s
[CV] n_estimators=1400, min_samples_split=10, min_samples_leaf=1, max_features=sqrt, max_depth=10, bootstrap=True 
[CV]  n_estimators=1200, min_samples_split=10, min_samples_leaf=4, max_features=0.3, max_depth=60, bootstrap=False, total=   2.5s
[CV] n_estimators=1400, min_samples_split=10, min_samples_leaf=1, max_features=sqrt, max_depth=10, bootstrap=True 
[CV]  n_estimators=1400, min_samples_split=10, min_samples_leaf=1, max_features=sqrt, max_depth=10, bootstrap=True, total=   2.9s
[CV] n_estimators=14

[Parallel(n_jobs=-1)]: Done 300 out of 300 | elapsed:  6.3min finished


RandomizedSearchCV(cv=3, error_score='raise',
          estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False),
          fit_params=None, iid=True, n_iter=100, n_jobs=-1,
          param_distributions={'n_estimators': [200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000], 'max_features': ['auto', 'sqrt', 0.3, 0.4], 'max_depth': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 110, None], 'min_samples_split': [2, 5, 10], 'min_samples_leaf': [1, 2, 4, 5, 10, 20], 'bootstrap': [True, False]},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring=None, verbose=2)

In [42]:
# vamos ver os melhores parâmetros retornados pela pesquisa randomica
rf_random.best_params_

{'n_estimators': 1600,
 'min_samples_split': 5,
 'min_samples_leaf': 2,
 'max_features': 0.4,
 'max_depth': 30,
 'bootstrap': True}

In [43]:
# Vamos usar esses valores
reset_rf_samples()
m = RandomForestClassifier(n_estimators=1600, n_jobs=-1, min_samples_split=5, min_samples_leaf=2, max_features=0.4, max_depth=30, bootstrap=True, oob_score= True)
m.fit(X_train, y_train)
print_score(m)

[0.9283707865168539, 0.8156424581005587, 0.8258426966292135]


### GridSearch com Cross Validation

O passo anterior nos permitiu descobrir os melhores valores dos parâmetros de forma randômica. Vamos usar agora uma técnica que faz a combinação dos melhores valores que informamos, utilizando todas as combinações possíveis.

PS.: Para acelerar esse processo, podemos utilizar subsampling.

In [46]:
from sklearn.model_selection import GridSearchCV
# Create the parameter grid based on the results of random search 
param_grid = {
    'bootstrap': [True, False],
    'max_depth': [30, 40, 60, 80, 90, 100, 150],
    'max_features': [0.3, 0.4, 'sqrt'],
    'min_samples_leaf': [1, 2, 5, 10, 15],
    'min_samples_split': [5, 8, 10, 12],
    'n_estimators': [50, 100, 200, 400, 500, 1000, 1500, 2000]
}
# Create a based model
rf = RandomForestClassifier()
# Instantiate the grid search model
grid_search = GridSearchCV(estimator = rf, param_grid = param_grid, cv = 3, n_jobs = -1, verbose = 2, scoring='accuracy')

In [47]:
# Fit the grid search to the data = 6720 combinações!
grid_search.fit(X_train, y_train)

Fitting 3 folds for each of 6720 candidates, totalling 20160 fits
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50 
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50, total=   0.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50, total=   0.3s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=100 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=50, total=   0.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=5, n_estimators=100 

[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=400 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=400, total=   1.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=400, total=   1.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500, total=   1.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500 


[Parallel(n_jobs=-1)]: Done  37 tasks      | elapsed:   28.8s


[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500, total=   1.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=500, total=   1.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1000, total=   2.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1000, total=   2.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=8, n_estimators=1500 
[CV]  bootstrap=True, max_depth=30, ma

[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=50, total=   0.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=50 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=50, total=   0.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=50 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=50, total=   0.1s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=100 
[CV]  bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=100, total=   0.2s
[CV] bootstrap=True, max_depth=30, max_features=0.3, min_samples_leaf=1, min_samples_split=12, n_estimators=100 
[CV]  bootstrap=True, max_depth=30, max_f

...

[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=100, total=   0.3s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=100 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=100, total=   0.3s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=100 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=100, total=   0.3s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=200 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=200, total=   0.5s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=5, n_estimators=200 
[CV]  bootst

[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=500 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=500, total=   1.1s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=500 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=500, total=   1.2s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=500, total=   1.1s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=1000 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=8, n_estimators=1000, total=   2.2s
[CV] boot

[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=10, n_estimators=2000 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=10, n_estimators=2000, total=   4.3s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=10, n_estimators=2000 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=10, n_estimators=2000, total=   4.2s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=12, n_estimators=50 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=12, n_estimators=50, total=   0.1s
[CV] bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=12, n_estimators=50 
[CV]  bootstrap=False, max_depth=150, max_features=sqrt, min_samples_leaf=15, min_samples_split=12, n_estimators=50, total=   0.1s
[CV]

[Parallel(n_jobs=-1)]: Done 20160 out of 20160 | elapsed: 293.8min finished


GridSearchCV(cv=3, error_score='raise',
       estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
            oob_score=False, random_state=None, verbose=0,
            warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'bootstrap': [True, False], 'max_depth': [30, 40, 60, 80, 90, 100, 150], 'max_features': [0.3, 0.4, 'sqrt'], 'min_samples_leaf': [1, 2, 5, 10, 15], 'min_samples_split': [5, 8, 10, 12], 'n_estimators': [50, 100, 200, 400, 500, 1000, 1500, 2000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='accuracy', verbose=2)

In [48]:
grid_search.best_params_

{'bootstrap': True,
 'max_depth': 40,
 'max_features': 0.4,
 'min_samples_leaf': 2,
 'min_samples_split': 5,
 'n_estimators': 400}

In [49]:
# Vamos usar esses valores
reset_rf_samples()
m = RandomForestClassifier(n_estimators=400, n_jobs=-1, min_samples_split=5, min_samples_leaf=2, max_features=0.4, max_depth=40, bootstrap=True, oob_score=True)
m.fit(X_train, y_train)
print_score(m)

[0.9297752808988764, 0.8212290502793296, 0.827247191011236]


In [50]:
len(df_test)

418

In [51]:
display_all(df_test)

Survived  Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  \
0         NaN       3    1  34.50      0      0     376    7.8292         1   
1         NaN       3    0  47.00      1      0     582    7.0000         2   
2         NaN       2    1  62.00      0      0     184    9.6875         1   
3         NaN       3    1  27.00      0      0     366    8.6625         2   
4         NaN       3    0  22.00      1      1     338   12.2875         2   
5         NaN       3    1  14.00      0      0     692    9.2250         2   
6         NaN       3    0  30.00      0      0     389    7.6292         1   
7         NaN       2    1  26.00      1      1     211   29.0000         2   
8         NaN       3    0  18.00      0      0     251    7.2292         0   
9         NaN       3    1  21.00      2      0     714   24.1500         2   
10        NaN       3    1    NaN      0      0     503    7.8958         2   
11        NaN       1    1  46.00      0      0     687   26.0000         2   
12        NaN       1    0  23.00      1      0     131   82.2667         2   
13        NaN       2    1  63.00      1      0     185   26.0000         2   
14        NaN       1    0  47.00      1      0     926   61.1750         2   
15        NaN       2    0  24.00      1      0     866   27.7208         0   
16        NaN       2    1  35.00      0      0     153   12.3500         1   
17        NaN       3    1  21.00      0      0     287    7.2250         0   
18        NaN       3    0  27.00      1      0     911    7.9250         2   
19        NaN       3    0  45.00      0      0     291    7.2250         0   
20        NaN       1    1  55.00      1      0     819   59.4000         0   
21        NaN       3    1   9.00      0      1     741    3.1708         2   
22        NaN       1    0    NaN      0      0     815   31.6833         2   
23        NaN       1    1  21.00      0      1     814   61.3792         0   
24        NaN       1    0  48.00      1      3     824  262.3750         0   
25        NaN       3    1  50.00      1      0     735   14.5000         2   
26        NaN       1    0  22.00      0      1      39   61.9792         0   
27        NaN       3    1  22.50      0      0     293    7.2250         0   
28        NaN       1    1  41.00      0      0      32   30.5000         2   
29        NaN       3    1    NaN      2      0     256   21.6792         0   
30        NaN       2    1  50.00      1      0     856   26.0000         2   
31        NaN       2    1  24.00      2      0     759   31.5000         2   
32        NaN       3    0  33.00      1      2     750   20.5750         2   
33        NaN       3    0    NaN      1      2     923   23.4500         2   
34        NaN       1    1  30.00      1      0      91   57.7500         0   
35        NaN       3    1  18.50      0      0     277    7.2292         0   
36        NaN       3    0    NaN      0      0     406    8.0500         2   
37        NaN       3    0  21.00      0      0     351    8.6625         2   
38        NaN       3    1  25.00      0      0     421    9.5000         2   
39        NaN       3    1    NaN      0      0     104   56.4958         2   
40        NaN       3    1  39.00      0      1     539   13.4167         0   
41        NaN       1    1    NaN      0      0      47   26.5500         2   
42        NaN       3    1  41.00      0      0     873    7.8500         2   
43        NaN       2    0  30.00      0      0     165   13.0000         2   
44        NaN       1    0  45.00      1      0      72   52.5542         2   
45        NaN       3    1  25.00      0      0     907    7.9250         2   
46        NaN       1    1  45.00      0      0     811   29.7000         0   
47        NaN       3    1    NaN      0      0     640    7.7500         1   
48        NaN       1    0  60.00      0      0      81   76.2917         0   
49        NaN       3    0  36.00      0      2     769

In [54]:
df, y, nas = proc_df(df_test, 'Survived')

In [55]:
display_all(df)

Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  \
0         3    1  34.50      0      0     376    7.8292         1   
1         3    0  47.00      1      0     582    7.0000         2   
2         2    1  62.00      0      0     184    9.6875         1   
3         3    1  27.00      0      0     366    8.6625         2   
4         3    0  22.00      1      1     338   12.2875         2   
5         3    1  14.00      0      0     692    9.2250         2   
6         3    0  30.00      0      0     389    7.6292         1   
7         2    1  26.00      1      1     211   29.0000         2   
8         3    0  18.00      0      0     251    7.2292         0   
9         3    1  21.00      2      0     714   24.1500         2   
10        3    1  27.00      0      0     503    7.8958         2   
11        1    1  46.00      0      0     687   26.0000         2   
12        1    0  23.00      1      0     131   82.2667         2   
13        2    1  63.00      1      0     185   26.0000         2   
14        1    0  47.00      1      0     926   61.1750         2   
15        2    0  24.00      1      0     866   27.7208         0   
16        2    1  35.00      0      0     153   12.3500         1   
17        3    1  21.00      0      0     287    7.2250         0   
18        3    0  27.00      1      0     911    7.9250         2   
19        3    0  45.00      0      0     291    7.2250         0   
20        1    1  55.00      1      0     819   59.4000         0   
21        3    1   9.00      0      1     741    3.1708         2   
22        1    0  27.00      0      0     815   31.6833         2   
23        1    1  21.00      0      1     814   61.3792         0   
24        1    0  48.00      1      3     824  262.3750         0   
25        3    1  50.00      1      0     735   14.5000         2   
26        1    0  22.00      0      1      39   61.9792         0   
27        3    1  22.50      0      0     293    7.2250         0   
28        1    1  41.00      0      0      32   30.5000         2   
29        3    1  27.00      2      0     256   21.6792         0   
30        2    1  50.00      1      0     856   26.0000         2   
31        2    1  24.00      2      0     759   31.5000         2   
32        3    0  33.00      1      2     750   20.5750         2   
33        3    0  27.00      1      2     923   23.4500         2   
34        1    1  30.00      1      0      91   57.7500         0   
35        3    1  18.50      0      0     277    7.2292         0   
36        3    0  27.00      0      0     406    8.0500         2   
37        3    0  21.00      0      0     351    8.6625         2   
38        3    1  25.00      0      0     421    9.5000         2   
39        3    1  27.00      0      0     104   56.4958         2   
40        3    1  39.00      0      1     539   13.4167         0   
41        1    1  27.00      0      0      47   26.5500         2   
42        3    1  41.00      0      0     873    7.8500         2   
43        2    0  30.00      0      0     165   13.0000         2   
44        1    0  45.00      1      0      72   52.5542         2   
45        3    1  25.00      0      0     907    7.9250         2   
46        1    1  45.00      0      0     811   29.7000         0   
47        3    1  27.00      0      0     640    7.7500         1   
48        1    0  60.00      0      0      81   76.2917         0   
49        3    0  36.00      0      2     769   15.9000         2   
50        1    1  24.00      1      0      98   60.0000         2   
51        2    1  27.00      0      0     867   15.0333         0   
52        2    0  20.00      2      1     320   23.0000         2   
53        1    0  28.00      3      2     123  263.0000         2   
54        2    1  27.00      0      0     853   15.5792         0   
55        3    1  10.00      4      1     659   29.1250         1   
56        3    1  35.00      0      0     513    7.8958         2   
57 

In [56]:
df.drop(columns=['Age_na','Fare_na'], inplace=True)

In [44]:
display_all(df)

Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked
0         3    1  34.50      0      0     152    7.8292         1
1         3    0  47.00      1      0     221    7.0000         2
2         2    1  62.00      0      0      73    9.6875         1
3         3    1  27.00      0      0     147    8.6625         2
4         3    0  22.00      1      1     138   12.2875         2
5         3    1  14.00      0      0     261    9.2250         2
6         3    0  30.00      0      0     158    7.6292         1
7         2    1  26.00      1      1      84   29.0000         2
8         3    0  18.00      0      0     100    7.2292         0
9         3    1  21.00      2      0     269   24.1500         2
10        3    1  27.00      0      0     195    7.8958         2
11        1    1  46.00      0      0     259   26.0000         2
12        1    0  23.00      1      0      52   82.2667         2
13        2    1  63.00      1      0      74   26.0000         2
14        1    0  47.00      1      0     362   61.1750         2
15        2    0  24.00      1      0     343   27.7208         0
16        2    1  35.00      0      0      60   12.3500         1
17        3    1  21.00      0      0     119    7.2250         0
18        3    0  27.00      1      0     356    7.9250         2
19        3    0  45.00      0      0     120    7.2250         0
20        1    1  55.00      1      0     316   59.4000         0
21        3    1   9.00      0      1     277    3.1708         2
22        1    0  27.00      0      0     314   31.6833         2
23        1    1  21.00      0      1     313   61.3792         0
24        1    0  48.00      1      3     319  262.3750         0
25        3    1  50.00      1      0     273   14.5000         2
26        1    0  22.00      0      1      14   61.9792         0
27        3    1  22.50      0      0     121    7.2250         0
28        1    1  41.00      0      0      11   30.5000         2
29        3    1  27.00      2      0     104   21.6792         0
30        2    1  50.00      1      0     338   26.0000         2
31        2    1  24.00      2      0     283   31.5000         2
32        3    0  33.00      1      2     280   20.5750         2
33        3    0  27.00      1      2     360   23.4500         2
34        1    1  30.00      1      0      34   57.7500         0
35        3    1  18.50      0      0     115    7.2292         0
36        3    0  27.00      0      0     166    8.0500         2
37        3    0  21.00      0      0     141    8.6625         2
38        3    1  25.00      0      0     172    9.5000         2
39        3    1  27.00      0      0      39   56.4958         2
40        3    1  39.00      0      1     204   13.4167         0
41        1    1  27.00      0      0      16   26.5500         2
42        3    1  41.00      0      0     347    7.8500         2
43        2    0  30.00      0      0      65   13.0000         2
44        1    0  45.00      1      0      24   52.5542         2
45        3    1  25.00      0      0     355    7.9250         2
46        1    1  45.00      0      0     312   29.7000         0
47        3    1  27.00      0      0     243    7.7500         1
48        1    0  60.00      0      0      30   76.2917         0
49        3    0  36.00      0      2     290   15.9000         2
50        1    1  24.00      1      0      37   60.0000         2
51        2    1  27.00      0      0     344   15.0333         0
52        2    0  20.00      2      1     131   23.0000         2
53        1    0  28.00      3      2      49  263.0000         2
54        2    1  27.00      0      0     335   15.5792         0
55        3    1  10.00      4      1     249   29.1250         1
56        3    1  35.00      0      0     198    7.8958         2
57        3    1  25.00      0      0     191    7.6500         2
58        3    1  27.00      1      0     253   16.1000         2
59        1    0  36.00      0      0     319

In [57]:
predictions = m.predict(df)

In [85]:
type(predictions)

numpy.ndarray

In [58]:
df['Survived'] = pd.Series(predictions)
display_all(df)

Pclass  Sex    Age  SibSp  Parch  Ticket      Fare  Embarked  \
0         3    1  34.50      0      0     376    7.8292         1   
1         3    0  47.00      1      0     582    7.0000         2   
2         2    1  62.00      0      0     184    9.6875         1   
3         3    1  27.00      0      0     366    8.6625         2   
4         3    0  22.00      1      1     338   12.2875         2   
5         3    1  14.00      0      0     692    9.2250         2   
6         3    0  30.00      0      0     389    7.6292         1   
7         2    1  26.00      1      1     211   29.0000         2   
8         3    0  18.00      0      0     251    7.2292         0   
9         3    1  21.00      2      0     714   24.1500         2   
10        3    1  27.00      0      0     503    7.8958         2   
11        1    1  46.00      0      0     687   26.0000         2   
12        1    0  23.00      1      0     131   82.2667         2   
13        2    1  63.00      1      0     185   26.0000         2   
14        1    0  47.00      1      0     926   61.1750         2   
15        2    0  24.00      1      0     866   27.7208         0   
16        2    1  35.00      0      0     153   12.3500         1   
17        3    1  21.00      0      0     287    7.2250         0   
18        3    0  27.00      1      0     911    7.9250         2   
19        3    0  45.00      0      0     291    7.2250         0   
20        1    1  55.00      1      0     819   59.4000         0   
21        3    1   9.00      0      1     741    3.1708         2   
22        1    0  27.00      0      0     815   31.6833         2   
23        1    1  21.00      0      1     814   61.3792         0   
24        1    0  48.00      1      3     824  262.3750         0   
25        3    1  50.00      1      0     735   14.5000         2   
26        1    0  22.00      0      1      39   61.9792         0   
27        3    1  22.50      0      0     293    7.2250         0   
28        1    1  41.00      0      0      32   30.5000         2   
29        3    1  27.00      2      0     256   21.6792         0   
30        2    1  50.00      1      0     856   26.0000         2   
31        2    1  24.00      2      0     759   31.5000         2   
32        3    0  33.00      1      2     750   20.5750         2   
33        3    0  27.00      1      2     923   23.4500         2   
34        1    1  30.00      1      0      91   57.7500         0   
35        3    1  18.50      0      0     277    7.2292         0   
36        3    0  27.00      0      0     406    8.0500         2   
37        3    0  21.00      0      0     351    8.6625         2   
38        3    1  25.00      0      0     421    9.5000         2   
39        3    1  27.00      0      0     104   56.4958         2   
40        3    1  39.00      0      1     539   13.4167         0   
41        1    1  27.00      0      0      47   26.5500         2   
42        3    1  41.00      0      0     873    7.8500         2   
43        2    0  30.00      0      0     165   13.0000         2   
44        1    0  45.00      1      0      72   52.5542         2   
45        3    1  25.00      0      0     907    7.9250         2   
46        1    1  45.00      0      0     811   29.7000         0   
47        3    1  27.00      0      0     640    7.7500         1   
48        1    0  60.00      0      0      81   76.2917         0   
49        3    0  36.00      0      2     769   15.9000         2   
50        1    1  24.00      1      0      98   60.0000         2   
51        2    1  27.00      0      0     867   15.0333         0   
52        2    0  20.00      2      1     320   23.0000         2   
53        1    0  28.00      3      2     123  263.0000         2   
54        2    1  27.00      0      0     853   15.5792         0   
55        3    1  10.00      4      1     659   29.1250         1   
56        3    1  35.00      0      0     513    7.8958         2   
57 

In [61]:
df_temp = pd.read_csv(f'{PATH}test.csv')

In [62]:
df_temp.tail()

PassengerId  Pclass                          Name     Sex   Age  SibSp  \
413         1305       3            Spector, Mr. Woolf    male   NaN      0   
414         1306       1  Oliva y Ocana, Dona. Fermina  female  39.0      0   
415         1307       3  Saether, Mr. Simon Sivertsen    male  38.5      0   
416         1308       3           Ware, Mr. Frederick    male   NaN      0   
417         1309       3      Peter, Master. Michael J    male   NaN      1   

     Parch              Ticket      Fare Cabin Embarked  
413      0           A.5. 3236    8.0500   NaN        S  
414      0            PC 17758  108.9000  C105        C  
415      0  SOTON/O.Q. 3101262    7.2500   NaN        S  
416      0              359309    8.0500   NaN        S  
417      1                2668   22.3583   NaN        C

In [63]:
df_ouput = pd.DataFrame({ 'PassengerId': df_temp['PassengerId'],
                            'Survived': df['Survived'] }, dtype=int)
display_all(df_ouput)

PassengerId  Survived
0            892         0
1            893         0
2            894         0
3            895         0
4            896         1
5            897         0
6            898         1
7            899         0
8            900         1
9            901         0
10           902         0
11           903         0
12           904         1
13           905         0
14           906         1
15           907         1
16           908         0
17           909         0
18           910         0
19           911         1
20           912         0
21           913         0
22           914         1
23           915         0
24           916         1
25           917         0
26           918         1
27           919         0
28           920         0
29           921         0
30           922         0
31           923         0
32           924         1
33           925         0
34           926         1
35           927         0
36           928         0
37           929         0
38           930         0
39           931         1
40           932         0
41           933         0
42           934         0
43           935         1
44           936         1
45           937         0
46           938         0
47           939         0
48           940         1
49           941         1
50           942         1
51           943         0
52           944         1
53           945         1
54           946         0
55           947         0
56           948         0
57           949         0
58           950         0
59           951         1
60           952         0
61           953         0
62           954         0
63           955         1
64           956         0
65           957         1
66           958         1
67           959         0
68           960         0
69           961         1
70           962         1
71           963         0
72           964         0
73           965         0
74           966         1
75           967         0
76           968         0
77           969         1
78           970         0
79           971         1
80           972         1
81           973         0
82           974         0
83           975         0
84           976         0
85           977         0
86           978         1
87           979         0
88           980         1
89           981         1
90           982         0
91           983         0
92           984         1
93           985         0
94           986         0
95           987         0
96           988         1
97           989         0
98           990         0
99           991         0
100          992         1
101          993         0
102          994         0
103          995         0
104          996         1
105          997         0
106          998         0
107          999         0
108         1000         0
109         1001         0
110         1002         0
111         1003         1
112         1004         1
113         1005         1
114         1006         1
115         1007         0
116         1008         0
117         1009         1
118         1010         1
119         1011         1
120         1012         1
121         1013         0
122         1014         1
123         1015         0
124         1016         0
125         1017         1
126         1018         0
127         1019         1
128         1020         0
129         1021         0
130         1022         0
131         1023         0
132         1024         0
133         1025         0
134         1026         0
135         1027         0
136         1028         0
137         1029         0
138         1030         0
139         1031         0
140         1032         0
141         1033         1
142         1034         0
143         1035         0
144         1036         1
145         1037         0
146         1038         1
147      

In [64]:
df_ouput.to_csv(f'{PATH}preds_with_FamilySize.csv', index=False)

In [65]:
len(df_ouput)

418